# Comenzamos con el Nivel 1: Boids Clásicos.

Tu objetivo es lograr que un grupo de partículas (agentes) exhiba un comportamiento de enjambre orgánico. Si lo haces bien, parecerá una bandada de pájaros o un cardumen de peces. Si lo haces mal, parecerá un gas explotando o mosquitos borrachos.

In [36]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation

In [37]:
# --- PARÁMETROS DE SIMULACIÓN ---
WIDTH, HEIGHT = 100, 100   # Tamaño del mundo
NUM_BOIDS = 50             # Cantidad de agentes
VISUAL_RANGE = 10          # Radio de visión (qué tan lejos ven a sus vecinos)
SPEED_LIMIT = 1.5         # Velocidad máxima

# Factores de peso (Ajusta esto para cambiar el comportamiento)
COHESION_FACTOR = 0.01
ALIGNMENT_FACTOR = 0.1
SEPARATION_FACTOR = 0.2
MIN_DISTANCE = 8.0         # Distancia mínima para activar separación

In [38]:
# --- INICIALIZACIÓN ---
# Posiciones: Matriz (N x 2) -> [[x1, y1], [x2, y2], ...]
positions = np.random.rand(NUM_BOIDS, 2) * np.array([WIDTH, HEIGHT])
# Velocidades: Matriz (N x 2)
velocities = (np.random.rand(NUM_BOIDS, 2) - 0.5) * 10

In [39]:
def distance(pos1, pos2):
    """Calcula la distancia euclidiana entre dos puntos"""
    return np.linalg.norm(pos1 - pos2)

In [40]:
def compute_rules(boid_idx, positions, velocities):
    """
    AQUÍ ES DONDE OCURRE LA MAGIA (Y TU TRABAJO).
    Calcula los vectores de fuerza para un boid específico.
    """
    my_pos = positions[boid_idx]
    my_vel = velocities[boid_idx]

    # Vectores acumuladores (inicializan en 0,0)
    v_cohesion = np.zeros(2)
    v_separation = np.zeros(2)
    v_alignment = np.zeros(2)

    neighbors_count = 0

    for i in range(NUM_BOIDS):
        if i == boid_idx:
            continue # No compararse con uno mismo

        other_pos = positions[i]
        dist = distance(my_pos, other_pos)

        if dist < VISUAL_RANGE:
            # --- TU CÓDIGO AQUÍ ---

            # 1. REGLA DE COHESIÓN: Ir hacia el centro de masa de los vecinos
            # Acumula las posiciones de los vecinos
            # v_cohesion += ...
            v_cohesion += other_pos  # Ejemplo de acumulación para cohesión

            # 2. REGLA DE ALINEACIÓN: Igualar velocidad de los vecinos
            # Acumula las velocidades de los vecinos
            # v_alignment += ...
            v_alignment += velocities[i]  # Ejemplo de acumulación para alineación

            # 3. REGLA DE SEPARACIÓN: Evitar chocar si están muy cerca
            if dist < MIN_DISTANCE:
                # Calcular vector que aleja al boid del vecino
                # v_separation += ...
                diff = my_pos - other_pos  # Ejemplo de separación
                diff /= (dist*dist)  # una vez para normalizar (hacerlo unitario) y otra vez para que crezca si están cerca.
                v_separation += diff

            neighbors_count += 1

    if neighbors_count > 0:
        # --- PROCESAMIENTO FINAL DE VECTORES ---

        # A. COHESIÓN:
        # Divide por neighbors_count para obtener el centro promedio
        # Resta my_pos para obtener el vector HACIA ese centro
        # Multiplica por COHESION_FACTOR
        v_cohesion = (v_cohesion / neighbors_count) - my_pos
        v_cohesion *= COHESION_FACTOR

        # B. ALINEACIÓN:
        # Divide por neighbors_count para obtener velocidad promedio
        # Resta my_vel para obtener la diferencia de dirección
        # Multiplica por ALINEMENT_FACTOR
        v_alignment = (v_alignment / neighbors_count) - my_vel
        v_alignment *= ALIGNMENT_FACTOR

        # C. SEPARACIÓN:
        # Multiplica por SEPARATION_FACTOR
        # pass # Borra esto cuando escribas tu código
        v_separation *= SEPARATION_FACTOR

    return v_cohesion + v_alignment + v_separation

def update(frame):
    global positions, velocities

    # 1. Calcular nuevas velocidades basadas en reglas
    new_velocities = np.copy(velocities)
    for i in range(NUM_BOIDS):
        # Obtenemos el vector de cambio de las reglas
        rule_vector = compute_rules(i, positions, velocities)
        new_velocities[i] += rule_vector

        # Limitar velocidad (para que no aceleren al infinito)
        speed = np.linalg.norm(new_velocities[i])
        if speed > SPEED_LIMIT:
            new_velocities[i] = (new_velocities[i] / speed) * SPEED_LIMIT

    velocities = new_velocities

    # 2. Actualizar posiciones
    positions += velocities

    # 3. Condiciones de frontera (Wrap around / Pacman)
    positions = positions % np.array([WIDTH, HEIGHT])

    # Actualizar gráfica
    scat.set_offsets(positions)
    # Orientar los triángulos según la velocidad (opcional, solo visual)
    return scat,

# # --- CONFIGURACIÓN GRÁFICA ---
# fig, ax = plt.subplots(figsize=(6, 6))
# ax.set_xlim(0, WIDTH)
# ax.set_ylim(0, HEIGHT)
# # Dibujamos los boids como triángulos azules
# scat = ax.scatter(positions[:, 0], positions[:, 1], marker='>', color='blue')

# animation = FuncAnimation(fig, update, interval=50)
# plt.show()

from IPython.display import HTML

# --- REINICIAR ESTADO (Pon esto al inicio de tu celda de ejecución) ---
positions = np.random.rand(NUM_BOIDS, 2) * np.array([WIDTH, HEIGHT])
velocities = (np.random.rand(NUM_BOIDS, 2) - 0.5) * 10

# --- CONFIGURACIÓN GRÁFICA ---
fig, ax = plt.subplots(figsize=(6, 6))
ax.set_xlim(0, WIDTH)
ax.set_ylim(0, HEIGHT)

# Dibujamos los boids
scat = ax.scatter(positions[:, 0], positions[:, 1], marker='>', color='blue')

def update_wrapper(frame):
    """Envoltorio para que funcione bien en el video"""
    return update(frame)

# 1. Agregamos 'frames=200' para que el video dure 200 pasos y corte (evita el warning)
# 2. interval=50 son milisegundos entre cuadros
animation = FuncAnimation(fig, update_wrapper, frames=500, interval=70, blit=True)

# ESTA ES LA CLAVE PARA NOTEBOOKS:
# Renderiza la animación como un componente HTML interactivo
plt.close() # Cierra la figura estática para no duplicar
HTML(animation.to_jshtml())